In [0]:
from pyspark.sql.functions import *

# Setting configuration To ADLS

In [0]:
spark.conf.set("fs.azure.account.key.riastore.dfs.core.windows.net","your_actual_key_here")

# DBUTILS

In [0]:
dbutils.fs.ls("abfss://bronze@riastore.dfs.core.windows.net/rawdata")

[FileInfo(path='abfss://bronze@riastore.dfs.core.windows.net/rawdata/data_08699269-8973-42ed-8e05-5cfa9b3dbb23_070beda2-e7e8-469a-8491-81b1eb123f84.parquet', name='data_08699269-8973-42ed-8e05-5cfa9b3dbb23_070beda2-e7e8-469a-8491-81b1eb123f84.parquet', size=152522, modificationTime=1749889979000),
 FileInfo(path='abfss://bronze@riastore.dfs.core.windows.net/rawdata/data_ab61c316-bec7-4a88-9ed2-33a5d0ad664b_30674add-23aa-4d2b-9da9-4d1ddf75526c.parquet', name='data_ab61c316-bec7-4a88-9ed2-33a5d0ad664b_30674add-23aa-4d2b-9da9-4d1ddf75526c.parquet', size=415, modificationTime=1749907085000),
 FileInfo(path='abfss://bronze@riastore.dfs.core.windows.net/rawdata/data_ad006dd3-a84d-45d8-ba61-95ec037bbffc_ec794b56-3480-475a-a45e-a1ef94e7a046.parquet', name='data_ad006dd3-a84d-45d8-ba61-95ec037bbffc_ec794b56-3480-475a-a45e-a1ef94e7a046.parquet', size=152522, modificationTime=1749888269000)]

#LOAD THE DATA

In [0]:
df = spark.read.parquet("abfss://bronze@riastore.dfs.core.windows.net/rawdata/data_08699269-8973-42ed-8e05-5cfa9b3dbb23_070beda2-e7e8-469a-8491-81b1eb123f84.parquet")

df.show()

+-----------+-----------+------------+---------+--------+--------+--------------------+--------------+--------+--------+------------+
|   Retailer|Retailer_ID|Invoice_Date|   Region|   State|    City|             Product|Price_per_Unit|Quantity|  Profit|Sales_Method|
+-----------+-----------+------------+---------+--------+--------+--------------------+--------------+--------+--------+------------+
|Foot Locker|    1185732|    1/2/2020|Northeast|New York|New York|Men's Athletic Fo...|            50|   1,000|  150000|    In-store|
|Foot Locker|    1185732|    1/3/2020|Northeast|New York|New York|Women's Street Fo...|            40|   1,000|  140000|    In-store|
|Foot Locker|    1185732|    1/4/2020|Northeast|New York|New York|Women's Athletic ...|            45|     850|  133875|    In-store|
|Foot Locker|    1185732|    1/5/2020|Northeast|New York|New York|       Men's Apparel|            60|     900|  162000|    In-store|
|Foot Locker|    1185732|    1/6/2020|Northeast|New York|New Y

#CLEANING

In [0]:
df = df.withColumn("Quantity", regexp_replace(df["Quantity"], "," , ""))
df.show()

+-----------+-----------+------------+---------+--------+--------+--------------------+--------------+--------+--------+------------+
|   Retailer|Retailer_ID|Invoice_Date|   Region|   State|    City|             Product|Price_per_Unit|Quantity|  Profit|Sales_Method|
+-----------+-----------+------------+---------+--------+--------+--------------------+--------------+--------+--------+------------+
|Foot Locker|    1185732|    1/2/2020|Northeast|New York|New York|Men's Athletic Fo...|            50|    1000|  150000|    In-store|
|Foot Locker|    1185732|    1/3/2020|Northeast|New York|New York|Women's Street Fo...|            40|    1000|  140000|    In-store|
|Foot Locker|    1185732|    1/4/2020|Northeast|New York|New York|Women's Athletic ...|            45|     850|  133875|    In-store|
|Foot Locker|    1185732|    1/5/2020|Northeast|New York|New York|       Men's Apparel|            60|     900|  162000|    In-store|
|Foot Locker|    1185732|    1/6/2020|Northeast|New York|New Y

# INTEGER CONVERSION


In [0]:

df = df.withColumn("Price_per_unit", df['Price_per_unit'].cast('float'))
df = df.withColumn("Quantity", df['Quantity'].cast('int'))
df = df.withColumn("Profit", df['Profit'].cast('float'))
df = df.withColumn("Invoice_Date", to_date(df['Invoice_Date'], 'M/d/yyyy'))
df = df.withColumn("Invoice_Month", month(df['Invoice_Date']))
df = df.withColumn("Invoice_Year",year(df['Invoice_Date']))
df = df.withColumn("Invoice_Day",day(df['Invoice_Date']))

display(df)

Retailer Retailer_ID Invoice_Date Region State City Product Price_per_unit Quantity Profit Sales_Method Invoice_Month Invoice_Year Invoice_Day Foot Locker 1185732 2020-01-02 Northeast New York New York Men's Athletic Footwear 50.0 1000 150000.0 In-store 1 2020 2 Foot Locker 1185732 2020-01-03 Northeast New York New York Women's Street Footwear 40.0 1000 140000.0 In-store 1 2020 3 Foot Locker 1185732 2020-01-04 Northeast New York New York Women's Athletic Footwear 45.0 850 133875.0 In-store 1 2020 4 Foot Locker 1185732 2020-01-05 Northeast New York New York Men's Apparel 60.0 900 162000.0 In-store 1 2020 5 Foot Locker 1185732 2020-01-06 Northeast New York New York Women's Apparel 50.0 1000 125000.0 In-store 1 2020 6 Foot Locker 1185732 2020-01-07 Northeast New York New York Men's Street Footwear 50.0 1250 312500.0 In-store 1 2020 7 Foot Locker 1185732 2020-01-08 Northeast New York New York Men's Athletic Footwear 50.0 900 135000.0 Outlet 1 2020 8 Foot Locker 1185732 2020-01-21 Northeast New York New York Women's Street Footwear 40.0 950 133000.0 Outlet 1 2020 21 Foot Locker 1185732 2020-01-22 Northeast New York New York Women's Athletic Footwear 45.0 825 129937.5 Outlet 1 2020 22 Foot Locker 1185732 2020-01-23 Northeast New York New York Men's Apparel 60.0 900 162000.0 Outlet 1 2020 23 Foot Locker 1185732 2020-01-24 Northeast New York New York Women's Apparel 50.0 1000 125000.0 Outlet 1 2020 24 Foot Locker 1185732 2020-01-25 Northeast New York New York Men's Street Footwear 50.0 1220 305000.0 Outlet 1 2020 25 Foot Locker 1185732 2020-01-26 Northeast New York New York Men's Athletic Footwear 50.0 925 138750.0 Outlet 1 2020 26 Foot Locker 1185732 2020-01-27 Northeast New York New York Women's Street Footwear 40.0 950 133000.0 Outlet 1 2020 27 Foot Locker 1185732 2020-01-28 Northeast New York New York Women's Athletic Footwear 45.0 800 126000.0 Outlet 1 2020 28 Foot Locker 1185732 2020-01-29 Northeast New York New York Men's Apparel 60.0 850 153000.0 Outlet 1 2020 29 Foot Locker 1185732 2020-01-30 Northeast New York New York Women's Apparel 50.0 950 118750.0 Outlet 1 2020 30 Foot Locker 1185732 2020-01-31 Northeast New York New York Men's Street Footwear 50.0 1200 300000.0 Outlet 1 2020 31 Foot Locker 1185732 2020-02-01 Northeast New York New York Men's Athletic Footwear 50.0 900 135000.0 Outlet 2 2020 1 Foot Locker 1185732 2020-02-02 Northeast New York New York Women's Street Footwear 40.0 900 126000.0 Outlet 2 2020 2 Foot Locker 1185732 2020-02-03 Northeast New York New York Women's Athletic Footwear 45.0 825 129937.5 Outlet 2 2020 3 Foot Locker 1185732 2020-02-04 Northeast New York New York Men's Apparel 60.0 825 148500.0 Outlet 2 2020 4 Foot Locker 1185732 2020-02-05 Northeast New York New York Women's Apparel 50.0 950 118750.0 Outlet 2 2020 5 Foot Locker 1185732 2020-02-06 Northeast New York New York Men's Street Footwear 60.0 1220 366000.0 Outlet 2 2020 6 Foot Locker 1185732 2020-02-07 Northeast New York New York Men's Athletic Footwear 55.0 925 152625.0 Outlet 2 2020 7 Foot Locker 1185732 2020-02-08 Northeast New York New York Women's Street Footwear 50.0 900 157500.0 Outlet 2 2020 8 Foot Locker 1185732 2020-02-09 Northeast New York New York Women's Athletic Footwear 50.0 850 148750.0 Outlet 2 2020 9 Foot Locker 1185732 2020-02-10 Northeast New York New York Men's Apparel 60.0 875 157500.0 Outlet 2 2020 10 Foot Locker 1185732 2020-03-03 Northeast New York New York Women's Apparel 65.0 1000 162500.0 Outlet 3 2020 3 Foot Locker 1185732 2020-03-04 Northeast New York New York Men's Street Footwear 60.0 1250 375000.0 Outlet 3 2020 4 Foot Locker 1185732 2020-03-05 Northeast New York New York Men's Athletic Footwear 55.0 1000 165000.0 Outlet 3 2020 5 Foot Locker 1185732 2020-03-06 Northeast New York New York Women's Street Footwear 50.0 925 161875.0 Outlet 3 2020 6 Foot Locker 1185732 2020-03-07 Northeast New York New York Women's Athletic Footwear 50.0 900 157500.0 Outlet 3 2020 7 Foot Locker 1185732 2020-03-08 Northeast New York

#SAVE THIS DATAFRAME TO SILVER LAYER

In [0]:
df.write.format("parquet").mode("overwrite").option("path","abfss://silver@riastore.dfs.core.windows.net/silverdata").save()

#SHOW SILVER DATA

In [0]:
%sql

select * from parquet.`abfss://silver@riastore.dfs.core.windows.net/silverdata`

Retailer Retailer_ID Invoice_Date Region State City Product Price_per_unit Quantity Profit Sales_Method Invoice_Month Invoice_Year Invoice_Day Foot Locker 1185732 2020-01-02 Northeast New York New York Men's Athletic Footwear 50.0 1000 150000.0 In-store 1 2020 2 Foot Locker 1185732 2020-01-03 Northeast New York New York Women's Street Footwear 40.0 1000 140000.0 In-store 1 2020 3 Foot Locker 1185732 2020-01-04 Northeast New York New York Women's Athletic Footwear 45.0 850 133875.0 In-store 1 2020 4 Foot Locker 1185732 2020-01-05 Northeast New York New York Men's Apparel 60.0 900 162000.0 In-store 1 2020 5 Foot Locker 1185732 2020-01-06 Northeast New York New York Women's Apparel 50.0 1000 125000.0 In-store 1 2020 6 Foot Locker 1185732 2020-01-07 Northeast New York New York Men's Street Footwear 50.0 1250 312500.0 In-store 1 2020 7 Foot Locker 1185732 2020-01-08 Northeast New York New York Men's Athletic Footwear 50.0 900 135000.0 Outlet 1 2020 8 Foot Locker 1185732 2020-01-21 Northeast New York New York Women's Street Footwear 40.0 950 133000.0 Outlet 1 2020 21 Foot Locker 1185732 2020-01-22 Northeast New York New York Women's Athletic Footwear 45.0 825 129937.5 Outlet 1 2020 22 Foot Locker 1185732 2020-01-23 Northeast New York New York Men's Apparel 60.0 900 162000.0 Outlet 1 2020 23 Foot Locker 1185732 2020-01-24 Northeast New York New York Women's Apparel 50.0 1000 125000.0 Outlet 1 2020 24 Foot Locker 1185732 2020-01-25 Northeast New York New York Men's Street Footwear 50.0 1220 305000.0 Outlet 1 2020 25 Foot Locker 1185732 2020-01-26 Northeast New York New York Men's Athletic Footwear 50.0 925 138750.0 Outlet 1 2020 26 Foot Locker 1185732 2020-01-27 Northeast New York New York Women's Street Footwear 40.0 950 133000.0 Outlet 1 2020 27 Foot Locker 1185732 2020-01-28 Northeast New York New York Women's Athletic Footwear 45.0 800 126000.0 Outlet 1 2020 28 Foot Locker 1185732 2020-01-29 Northeast New York New York Men's Apparel 60.0 850 153000.0 Outlet 1 2020 29 Foot Locker 1185732 2020-01-30 Northeast New York New York Women's Apparel 50.0 950 118750.0 Outlet 1 2020 30 Foot Locker 1185732 2020-01-31 Northeast New York New York Men's Street Footwear 50.0 1200 300000.0 Outlet 1 2020 31 Foot Locker 1185732 2020-02-01 Northeast New York New York Men's Athletic Footwear 50.0 900 135000.0 Outlet 2 2020 1 Foot Locker 1185732 2020-02-02 Northeast New York New York Women's Street Footwear 40.0 900 126000.0 Outlet 2 2020 2 Foot Locker 1185732 2020-02-03 Northeast New York New York Women's Athletic Footwear 45.0 825 129937.5 Outlet 2 2020 3 Foot Locker 1185732 2020-02-04 Northeast New York New York Men's Apparel 60.0 825 148500.0 Outlet 2 2020 4 Foot Locker 1185732 2020-02-05 Northeast New York New York Women's Apparel 50.0 950 118750.0 Outlet 2 2020 5 Foot Locker 1185732 2020-02-06 Northeast New York New York Men's Street Footwear 60.0 1220 366000.0 Outlet 2 2020 6 Foot Locker 1185732 2020-02-07 Northeast New York New York Men's Athletic Footwear 55.0 925 152625.0 Outlet 2 2020 7 Foot Locker 1185732 2020-02-08 Northeast New York New York Women's Street Footwear 50.0 900 157500.0 Outlet 2 2020 8 Foot Locker 1185732 2020-02-09 Northeast New York New York Women's Athletic Footwear 50.0 850 148750.0 Outlet 2 2020 9 Foot Locker 1185732 2020-02-10 Northeast New York New York Men's Apparel 60.0 875 157500.0 Outlet 2 2020 10 Foot Locker 1185732 2020-03-03 Northeast New York New York Women's Apparel 65.0 1000 162500.0 Outlet 3 2020 3 Foot Locker 1185732 2020-03-04 Northeast New York New York Men's Street Footwear 60.0 1250 375000.0 Outlet 3 2020 4 Foot Locker 1185732 2020-03-05 Northeast New York New York Men's Athletic Footwear 55.0 1000 165000.0 Outlet 3 2020 5 Foot Locker 1185732 2020-03-06 Northeast New York New York Women's Street Footwear 50.0 925 161875.0 Outlet 3 2020 6 Foot Locker 1185732 2020-03-07 Northeast New York New York Women's Athletic Footwear 50.0 900 157500.0 Outlet 3 2020 7 Foot Locker 1185732 2020-03-08 Northeast New York